---
# **Video Caption Generation Model** 
---

- 동영상을 입력 받으면 캡션이 생성 된 영상으로 최종 결과물 반환한다.
- 캡셔닝 된 동영상은 지정한 경로로 저장 된다.
- 추가적으로, 이곳에서 바로 출력해서 동영상을 확인 할 수도 있으며, GIF로 생성할 수도 있다.

In [ ]:
from google.colab import drive
drive.mount('/content/drive', force_remount=True)

Mounted at /content/drive


In [ ]:
# working directry 지정
%cd /content/drive/MyDrive/Colab Notebooks/video_captioning5
!pwd

/content/drive/MyDrive/Colab Notebooks/video_captioning5
/content/drive/MyDrive/Colab Notebooks/video_captioning5


## **Requirements**
- 라이브러리/패키지
- 한글 폰트 설치

In [ ]:
import os
import sys
import time
import shutil
import pickle
import random
from time import time
from tqdm import tqdm

import cv2
import numpy as np
import matplotlib.pyplot as plt
from PIL import Image, ImageFont, ImageDraw

from konlpy.tag import Kkma
from skimage.metrics import structural_similarity as ssim

import tensorflow
from tensorflow.keras.models import Model
import tensorflow.keras.preprocessing.image
import tensorflow.keras.applications.inception_v3
from tensorflow.keras.applications.inception_v3 import InceptionV3
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [ ]:
# konlpy 설치
!pip install konlpy

# 한글 폰트 사용 설치
!sudo apt-get install -y fonts-nanum
!sudo fc-cache -fv
!rm ~/.cache/matplotlib -rf

     |████████████████████████████████| 19.4 MB 4.1 MB/s 
     |████████████████████████████████| 448 kB 95.1 MB/s 
Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following packages were automatically installed and are no longer required:
  cuda-command-line-tools-10-0 cuda-command-line-tools-10-1
  cuda-command-line-tools-11-0 cuda-compiler-10-0 cuda-compiler-10-1
  cuda-compiler-11-0 cuda-cuobjdump-10-0 cuda-cuobjdump-10-1
  cuda-cuobjdump-11-0 cuda-cupti-10-0 cuda-cupti-10-1 cuda-cupti-11-0
  cuda-cupti-dev-11-0 cuda-documentation-10-0 cuda-documentation-10-1
  cuda-documentation-11-0 cuda-documentation-11-1 cuda-gdb-10-0 cuda-gdb-10-1
  cuda-gdb-11-0 cuda-gpu-library-advisor-10-0 cuda-gpu-library-advisor-10-1
  cuda-libraries-10-0 cuda-libraries-10-1 cuda-libraries-11-0
  cuda-memcheck-10-0 cuda-memcheck-10-1 cuda-memcheck-11-0 cuda-nsight-10-0
  cuda-nsight-10-1 cuda-nsight-11-0 cuda-nsight-11-1 cuda-nsight-compute-10-0
  cuda-n

## **캡션 생성을 위한 준비/세팅**
- 캡션 생성에 필요한 데이터 불러오기
- 추론에 필요한 정보/값 구하기 (wordtoidx, idxtoword, vocab_size, max_length)
- 학습된 모델 다시 불러오기

In [ ]:
# wordtoidx, idxtoword, vocab_size, max_length 구하기

# train descriptions 다시 불러오기
import pickle
with open("train_descriptions.pkl", "rb") as f:
    train_descriptions = pickle.load(f)

# 모든 (train용) descriptions(captions)을 리스트로 저장
# train data만 진행
all_train_captions = []
for key, val in train_descriptions.items():
    for cap in val:
        all_train_captions.append(cap)
print('all train descriptions:', len(all_train_captions))

# 빈도수가 지정한 숫자보다 적은 단어 제외
# 빈도수가 너무 적은 단어까지 포함시켜 학습을 하게 되면 시간이 많이 소요될 뿐만 아니라 정확도가 낮아질 수 있다.
word_count_threshold = 4
word_counts = {}
nsents = 0
for sent in all_train_captions:
    nsents += 1
    for w in sent.split(' '):
        word_counts[w] = word_counts.get(w, 0) + 1
vocab = [w for w in word_counts if word_counts[w] >= word_count_threshold]
print('preprocessed words %d ==> %d' % (len(word_counts), len(vocab)))

# 모든 {단어 : 인덱스 번호} 구하기
# wordtoidx / idxtoword 딕셔너리 생성
idxtoword = {} # {인덱스 : 단어}
wordtoidx = {} # {단어 : 인덱스}
ix = 1
for w in vocab:
    wordtoidx[w] = ix
    idxtoword[ix] = w
    ix += 1

# vocab size 구하기
# we append 1 to our vocabulary since we append 0’s to make all captions of equal length
vocab_size = len(idxtoword) + 1 
print('vocab size:', vocab_size)

# max_length 구하기
max_length = max(len(d.split()) for d in all_train_captions)
print('description max length: %d' % max_length)

# pre-trained Inception model 불러오기 및 학습
USE_INCEPTION = True

if USE_INCEPTION:
    encode_model = InceptionV3(weights='imagenet') #InceptionV3 사용
    encode_model = Model(encode_model.input, encode_model.layers[-2].output)
    WIDTH = 299
    HEIGHT = 299
    OUTPUT_DIM = 2048 #output : 2048 / OPUTPUT_DIM은 어떤 pre-trained CNN 모델을 쓰느냐에 따라 다르다
    preprocess_input = tensorflow.keras.applications.inception_v3.preprocess_input
else:
    encode_model = MobileNet(weights='imagenet',include_top=False)
    WIDTH = 224
    HEIGHT = 224
    OUTPUT_DIM = 50176
    preprocess_input = tensorflow.keras.applications.mobilenet.preprocess_input

# 이미지 전처리 및 인코딩 함수
# 이미지 전처리, 파라미터 값 지정, 그리고 벡터로 변환
def encodeImage(img):
    # 이미지 사이즈를 표준크기로 재조정
    img = img.resize((WIDTH, HEIGHT), Image.ANTIALIAS) # eshape the images to (299 x 299) since we are using InceptionV3
    #  PIL 이미지를 numpy array로 변경; Convert PIL image to numpy array of 3-dimensions
    x = tensorflow.keras.preprocessing.image.img_to_array(img)
    # 2D array로 확장; Add one more dimension
    x = np.expand_dims(x, axis=0)
    # InceptionV3의 인풋을 위한 전처리; preprocess images using preprocess_input() from inception module
    x = preprocess_input(x)
    # 인코딩 벡터 반환
    x = encode_model.predict(x)
    # LSTM을 입력을 위한 shape 조정
    x = np.reshape(x, OUTPUT_DIM) # reshape from (1, 2048) to (2048, ); np.reshape(x, x.shape[1])
    return x

# 저장한 prediction 모델 다시 불러오기
from tensorflow import keras
model = keras.models.load_model('caption_generation_model.h5')

all train descriptions: 414113
preprocessed words 21604 ==> 10460
vocab size: 10461
description max length: 57
96124928/96112376 [==============================] - 4s 0us/step


## **필요한 함수들 생성**

캡션 출력 함수
- Greedy Search
- Beam Search

이미지 유사도 측정 함수
- MSE
- SSIM

In [ ]:
# Greedy Search prediction
def greedy_search_prediction(photo):
    # seed the generation process
    in_text = 'startseq'
    # iterate over the whole length of the sequence
    for i in range(max_length):
        sequence = [wordtoidx[w] for w in in_text.split() if w in wordtoidx] # encode the input sequence to integer
        sequence = pad_sequences([sequence], maxlen=max_length) # pad the input; padding
        yhat = model.predict([photo, sequence], verbose=0) # predict next word
        yhat = np.argmax(yhat) # convert probability to integer
        word = idxtoword[yhat] # map/convert integer to word/text
        # stop if we cannot map the word
        if word is None:
            break
        # append as another input for generating the next word
        in_text += ' ' + word
        # stop if we predict the end of the sequence
        if word == 'endseq':
            break
    final = in_text.split()
    final = final[1:-1]
    final = ' '.join(final)
    return final

# Beam Search prediction
def beam_search_prediction(image, beam_index = 3):
    start = [wordtoidx["startseq"]]
    start_word = [[start, 0.0]]
    while len(start_word[0][0]) < max_length:
        temp = []
        for s in start_word:
            par_caps = pad_sequences([s[0]], maxlen=max_length, padding='post')
            preds = model.predict([image,par_caps], verbose=0)
            word_preds = np.argsort(preds[0])[-beam_index:]
            # Getting the top <beam_index>(n) predictions and creating a 
            # new list so as to put them via the model again
            for w in word_preds:
                next_cap, prob = s[0][:], s[1]
                next_cap.append(w)
                prob += preds[0][w]
                temp.append([next_cap, prob])   
        start_word = temp
        # Sorting according to the probabilities
        start_word = sorted(start_word, reverse=False, key=lambda l: l[1])
        # Getting the top words
        start_word = start_word[-beam_index:]
    start_word = start_word[-1][0]
    intermediate_caption = [idxtoword[i] for i in start_word]
    final_caption = []
    for i in intermediate_caption:
        if i != 'endseq':
            final_caption.append(i)
        else:
            break
    final_caption = ' '.join(final_caption[1:])
    return final_caption

# 이미지 유사도 측정 - mse
def mse(imageA, imageB):
    # the 'Mean Squared Error' between the two images is the sum of the squared difference between the two images;
    # NOTE: the two images must have the same dimension
    err = np.sum((imageA.astype("float") - imageB.astype("float")) ** 2)
    err /= float(imageA.shape[0] * imageA.shape[1])
    # return the MSE, the lower the error, the more "similar" the two images are
    return err

# 이미지 유사도 측정 - ssim
def compare_images(imageA, imageB):
    # compute the mean squared error and structural similarity index for the images
    #m = mse(imageA, imageB)
    s = ssim(imageA, imageB)
    return s

## **비디오 캡션 생성**
- OpenCV 사용
- Pillow 사용

```
1. OpenCV를 사용하여 입력된 동영상을 frame으로 나누기
2. 나눠진 각 frame에 대해 이미지 캡셔닝 모델을 사용하여 한국어 캡션을 생성
3. 생성된 한국어 캡션을 frame 이미지에 출력하기 위해 Pillow 사용
4. 다시 OpenCV를 사용하여 frame 이미지들을 다시 동영상으로 변환
```

### (1) 동영상 frame 이미지를 별도 파일로 저장하지 않고 처리

In [ ]:
# Video caption generation

# 영상을 입력 받으면 frame 이미지들로 나눠서 captioning 처리
# frame 이미지들은 별도로 폴더에 저장하지 않고 바로 처리
# caption generate 된 영상으로 최종 결과물 반환

start_time = time.time()

# =================================================================================================
# read video file
video_name = 'your_video_file_name' # 동영상 파일 이름
base_path = '/content/drive/MyDrive/Colab Notebooks' # 기본 경로 입력

video_id = video_name + '.mp4' # .avi 등 읽어들일 동영상 파일 형식에 맞게 입력
video_path = os.path.join(base_path, video_id) # 동영상 파일 경로
cap = cv2.VideoCapture(video_path)

# =================================================================================================
# video에서 frame image 추출
print('extracting video frame images...')

count = 0
image_dict = {}
while cap.isOpened():
    ret, frame = cap.read()
    if ret is False:
        break
    image_id = 'frame_{}.jpg'.format(count)
    image_dict[image_id] = frame
    count += 1
cap.release()
cv2.destroyAllWindows()

print('total video frame images:', count)

# =================================================================================================
# frame 이미지들 특성 추출
print('extracting features from video frame images...')

test_features = {}
for i in tqdm(range(len(image_dict))):
    image_id = 'frame_{}.jpg'.format(i)
    
    # 이미지 배열을 pillow format에 적합하게 변환 
    image_arrays = cv2.cvtColor(image_dict[image_id], cv2.COLOR_BGR2RGB) # keras는 RGB format으로 이미지를 읽는다
        #.astype(np.uint8)?; cv2.imread usually reads in images in uint8 precision
        # Numpy data for 3-channel color images always has to have dtype=np.uint8
        # RGB/BGR images are usually encoded in 3-channel numpy uint8 arrays
    
    # load and change numpy array of image into image in Pillow format, PIL Image instance
    img = tensorflow.keras.preprocessing.image.array_to_img(image_arrays) # default: scale=True, dtype=None(float32)
        # "Examining the output of  keras loaded image, you can see that the data is in floating point precision 
        # so you may also want to convert to a floating-point representation, such as float32"
        # ==> keras array_to_img()는 default로 'float32'로 읽어오는 것 같다
    
    # frame 이미지별 특성 저장
    test_features[image_id] = encodeImage(img)

print('total extracted image features:', len(test_features))

# =================================================================================================
# caption generation 및 video 생성
print('generating captions...')

kkma = Kkma()
img_array = []
prev_img = []
for i in tqdm(range(len(image_dict))): 

    # 이미지 id
    image_id = 'frame_{}.jpg'.format(i)

    # 이미지 load
    img = image_dict[image_id] # .astype(np.uint8)
    if img is None:
        print('Image load failed!')
        sys.exit()

    # 입력받은 이미지의 특성 불러오기
    image_feature = test_features[image_id].reshape((1,OUTPUT_DIM)) # OUTPUT_DIM = 2048

    # 이미지 width, height 저장
    height, width, layers = img.shape
    size = (width, height)
    
    # 이미지 유사도 분석을 위한 gray image
    img_gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
        
    # OpenCV에선 한글 깨짐 발생; 한글 캡션 출력을 위해 Pillow 사용
    # img 배열을 Pillow가 처리 가능하게 변환
    img = Image.fromarray(cv2.cvtColor(img, cv2.COLOR_BGR2RGB))

    # 읽어들인 이미지에 caption 삽입 시작
    draw = ImageDraw.Draw(img) # PIL ImageDraw 객체 생성
    fontsize = round(height * 0.02)
    font = ImageFont.truetype('./fonts/NanumGothic.ttf', fontsize) # 사용할 한글 폰트 및 글자 크기 지정

    # pick greedy search (True) / beam search (False)
    use_greedy = True
    
    # beam search 사용시 사용할 beam_index 설정
    if use_greedy == False:
        beam_index = 3

    if not len(prev_img):
        prev_img = img_gray

        if use_greedy == True:
            greedy_caption = greedy_search_prediction(image_feature)
            greedy_caption = ''.join(greedy_caption.split(' '))
            greedy_caption = ' '.join(kkma.sentences(greedy_caption)) # sentence detection
            prev_greedy_caption = greedy_caption
        else:
            beam_caption = beam_search_prediction(image_feature, beam_index=beam_index)
            beam_caption = ''.join(beam_caption.split(' '))
            beam_caption = ' '.join(kkma.sentences(beam_caption)) # sentence detection
            prev_beam_caption = beam_caption
    
    else:
        ssim_result = compare_images(prev_img, img_gray) # 이미지 유사도 측정
        prev_img = img_gray
        
        if ssim_result >= 0.80: # 이미지 유사도 threshold
            if use_greedy == True:
                greedy_caption = prev_greedy_caption
            else:
                beam_caption = prev_beam_caption
        else:
            if use_greedy == True:
                greedy_caption = greedy_search_prediction(image_feature)
                greedy_caption = ''.join(greedy_caption.split(' '))
                greedy_caption = ' '.join(kkma.sentences(greedy_caption))
                prev_greedy_caption = greedy_caption
            else:
                beam_caption = beam_search_prediction(image_feature, beam_index=beam_index)
                beam_caption = ''.join(beam_caption.split(' '))
                beam_caption = ' '.join(kkma.sentences(beam_caption))
                prev_beam_caption = beam_caption

    if use_greedy == True:
        caption = greedy_caption
    else:
        caption = beam_caption
    
    text_w, text_h = draw.textsize(caption, font) # 캡션 글자의 width, height
    org = ((width-text_w)/2, (height*0.9)) # 캡션 위치 설정
    draw.text(org, caption, font=font, fill=(255,255,255)) # (255,255,255): 글자 색 흰색으로 설정

    # 다시 OpenCV가 처리가능하게 numpy 배열 및 BGR로 변환
    img = cv2.cvtColor(np.array(img), cv2.COLOR_RGB2BGR)

    # img_array에 append
    img_array.append(img)

# =================================================================================================
# 비디오 writer 객체 생성
print('creating captioned video...')

captioned_video_name = 'captioned_' + video_name + '.avi'
out = cv2.VideoWriter(captioned_video_name, # mp4가 조금 더 확장성이 있음; 모든 기기와 호환
                      cv2.VideoWriter_fourcc(*'DIVX'), 30, size) 
# fourcc: 동영상 파일의 codec, 압축 방식, 색상, 픽셀 포맷 등을 정의하는 정수 값 / fps: 초당 프레임 수 / size: 저장될 사이즈
# 화질을 결정하는 것은 코덱; 다른 코덱을 사용한 시도도 고려 -- DIVX, XVID, MJPG, X264, WMV1, WMV2 등 (참고로, 각 OS마다 지원하는 codec 다르다)

# 비디오 생성
for i in range(len(img_array)):
    out.write(img_array[i]) # out.write(frame)을 호출하면 현재 frame이 저장
out.release()

print('video captioning completed')
print("--- %s seconds ---" % (time.time() - start_time))

extracting video frame images...
total video frame images: 377
extracting features from video frame images...


100%|██████████| 377/377 [00:24<00:00, 15.10it/s]


total extracted image features: 377
generating captions...


100%|██████████| 377/377 [01:27<00:00,  4.31it/s]


creating captioned video...
video captioning completed
--- 113.89657807350159 seconds ---


### (2) 동영상 frame 이미지를 별도 파일로 저장하여 처리
- 처음에 구현한 방법
- 각 frame 이미지를 물리적으로 저장하고자 한다면 이 (2)번 방법을 사용
- 저장공간 효율성과 처리 시간 단축을 위해 frame 이미지를 별도 파일로 저장하지 않고 처리하게 만든 것이 (1)번 방법

In [ ]:
# video caption generation #2

# 동영상을 입력으로 받아 frame으로 나누고 frame image를 별도 파일로 저장 후 처리하여 caption 생성
# 이미지들에 대한 추출한 특성도 pickle로 저장
# caption generate 된 동영상으로 최종 결과물 반환

start_time = time.time()

# 동영상 파일 이름
video_name = 'your_video_file_name' # 동영상 파일 이름 입력

# video에서 추출한 frame image들을 저장할 디렉토리 생성
base_path = '/content/drive/MyDrive/Colab Notebooks' # 기본 경로 입력
test_video_frame_folder = video_name + '_' + 'frames'
video_frames_dir_path = os.path.join(base_path, test_video_frame_folder)
if os.path.exists(video_frames_dir_path):
    shutil.rmtree(video_frames_dir_path)
os.makedirs(video_frames_dir_path)

# =================================================================================================
# read video file
video_id = video_name + '.mp4' # .avi 등 읽어들일 동영상 파일 형식에 맞게 입력
video_path = os.path.join(base_path, video_id)
cap = cv2.VideoCapture(video_path)

# =================================================================================================
# video에서 frame image 추출
print('extracting video frame images...')

count = 0
image_list = []
while cap.isOpened():
    ret, frame = cap.read()
    if ret is False:
        break
    # 이미지로 생성된 각 frame을 디렉토리에 저장
    cv2.imwrite(os.path.join(base_path, test_video_frame_folder, 'frame_%d.jpg'%count), frame)
    # 생성된 각 frame 이미지들 이름을 리스트에 저장
    image_list.append(os.path.join(base_path, test_video_frame_folder, 'frame_%d.jpg'%count))
    count += 1

cap.release()
cv2.destroyAllWindows()
print('total video frame images:', count)

# =================================================================================================
# frame 이미지들 특성 추출
print('extracting features from video frame images...')

test_path = os.path.join(base_path,f'video_frame_image_features_{video_name}.pkl')

if not os.path.exists(test_path):
    test_features = {}
    for i in tqdm(range(len(image_list))):
        image_id = 'frame_{}.jpg'.format(i)
        image_path = os.path.join(base_path, test_video_frame_folder, image_id)
        img = tensorflow.keras.preprocessing.image.load_img(image_path, target_size=(HEIGHT, WIDTH))
        test_features[image_id] = encodeImage(img)
    # 이미지 특성 추출한 것을 pickle로 저장
    with open(test_path, "wb") as fp:
        pickle.dump(test_features, fp)
# 추출된 이미지 특성이 이미 있다면, 해당 pickle 파일 불러오기
else: 
    with open(test_path, "rb") as fp:
        test_features = pickle.load(fp)
print('total extracted image features:', len(test_features))

# =================================================================================================
# caption generation 및 video 생성
print('generating captions...')

kkma = Kkma()
images_path = os.path.join(base_path, test_video_frame_folder)

img_array = []
prev_img = []

# 이미지 순서대로 반복문 돌리며 캡션 생성
for image_file in tqdm(sorted(os.scandir(images_path), key=lambda f: int(f.name.replace('frame_','').replace('.jpg', '')))):

    # 각 이미지에 대한 반복문 실행
    if image_file.is_file() and image_file.name.startswith('frame_'):
        # 이미지 경로 및 id
        path_to_image = image_file.path
        image_id = image_file.name
        
        # 입력받은 이미지 특성 가져오고 caption 생성
        image_feature = test_features[image_id].reshape((1,OUTPUT_DIM)) # OUTPUT_DIM = 2048
        
        # 이미지 load
        img = cv2.imread(path_to_image)
        if img is None:
            print('Image load failed!')
            sys.exit()
        
        # 이미지 width, height 저장
        height, width, layers = img.shape
        size = (width, height)
        
        # 이미지 유사도 분석을 위한 gray image
        img_gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
            
        # OpenCV에선 한글 깨짐 발생; 한글 캡션 출력을 위해 Pillow 사용
        # img 배열을 Pillow가 처리 가능하게 변환
        img = Image.fromarray(cv2.cvtColor(img, cv2.COLOR_BGR2RGB))

        # 읽어들인 이미지에 caption 삽입
        draw = ImageDraw.Draw(img) # PIL ImageDraw 객체 생성
        fontsize = round(height * 0.02)
        font = ImageFont.truetype('./fonts/NanumGothic.ttf', fontsize) # 사용할 한글 폰트 및 글자 크기 지정

        # pick greedy search (True) / beam search (False)
        use_greedy = True
        
        # beam search 사용시 사용할 beam_index 설정
        if use_greedy == False:
            beam_index = 3

        if not len(prev_img):
            prev_img = img_gray

            if use_greedy == True:
                greedy_caption = greedy_search_prediction(image_feature)
                greedy_caption = ''.join(greedy_caption.split(' '))
                greedy_caption = ' '.join(kkma.sentences(greedy_caption)) # sentence detection
                prev_greedy_caption = greedy_caption
            else:
                beam_caption = beam_search_prediction(image_feature, beam_index=beam_index)
                beam_caption = ''.join(beam_caption.split(' '))
                beam_caption = ' '.join(kkma.sentences(beam_caption)) # sentence detection
                prev_beam_caption = beam_caption
        
        else:
            ssim_result = compare_images(prev_img, img_gray) # 이미지 유사도 측정
            prev_img = img_gray
            
            if ssim_result >= 0.80: # 이미지 유사도 threshold
                if use_greedy == True:
                    greedy_caption = prev_greedy_caption
                else:
                    beam_caption = prev_beam_caption
            else:
                if use_greedy == True:
                    greedy_caption = greedy_search_prediction(image_feature)
                    greedy_caption = ''.join(greedy_caption.split(' '))
                    greedy_caption = ' '.join(kkma.sentences(greedy_caption))
                    prev_greedy_caption = greedy_caption
                else:
                    beam_caption = beam_search_prediction(image_feature, beam_index=beam_index)
                    beam_caption = ''.join(beam_caption.split(' '))
                    beam_caption = ' '.join(kkma.sentences(beam_caption))
                    prev_beam_caption = beam_caption

        if use_greedy == True:
            caption = greedy_caption
        else:
            caption = beam_caption

        text_w, text_h = draw.textsize(caption, font) # 캡션 글자의 width, height
        org = ((width-text_w)/2, (height*0.9)) # 캡션 위치 설정
        draw.text(org, caption, font=font, fill=(255,255,255)) # (255,255,255): 글자 색 흰색으로 설정

        # 다시 OpenCV가 처리가능한 np 배열로 변환
        img = cv2.cvtColor(np.array(img), cv2.COLOR_RGB2BGR)

        # img_array에 append
        img_array.append(img)

# =================================================================================================
# 비디오 writer 객체 생성
print('creating captioned video...')

captioned_video_name = 'captioned_' + video_name + '.avi'
out = cv2.VideoWriter(captioned_video_name, # mp4가 조금 더 확장성이 있음; 모든 기기와 호환
                      cv2.VideoWriter_fourcc(*'DIVX'), 30, size)
# fourcc: 동영상 파일의 codec, 압축 방식, 색상, 픽셀 포맷 등을 정의하는 정수 값 / fps: 초당 프레임 수 / size: 저장될 사이즈
# 화질을 결정하는 것은 코덱; 다른 코덱을 사용한 시도도 고려 -- DIVX, XVID, MJPG, X264, WMV1, WMV2 등 (참고로, 각 OS마다 지원하는 codec 다르다)

# 비디어 생성
for i in range(len(img_array)):
    out.write(img_array[i]) # out.write(frame)을 호출하면 현재 frame이 저장
out.release()

print('video captioning completed')
print("--- %s seconds ---" % (time.time() - start_time))

---

**동영상 바로 출력 또는 GIF 생성**
- 최종 결과물인 캡셔닝 된 동영상은 지정한 경로에서 확인 가능하다.
- 하지만 이곳에서 바로 출력해서도 보고싶거나, GIF로 만들고 싶다면 Moviepy를 사용하면 된다.

In [ ]:
!pip install moviepy

### **Moviepy로 동영상 바로 출력하기**

In [ ]:
from moviepy.editor import *

path="/content/drive/MyDrive/Colab Notebooks/video_captioning/test.avi" 

clip=VideoFileClip(path)
clip.ipython_display(width=500)

100%|██████████| 309/309 [00:05<00:00, 58.47it/s]


### **Moviepy로 동영상 GIF로 만들기**

In [ ]:
# Import everything needed to edit video clips
from moviepy.editor import *

# loading video dsa gfg intro video
clip = VideoFileClip("/content/drive/MyDrive/Colab Notebooks/video_captioning5/test_video_captioning/captioned_Cat_65438_n3.avi")
  
# getting only first 3 seconds
#clip = clip.subclip(6,34)

# resize and applying speed effect
# clip.fx( vfx.speedx, 0.5) # slower
clip = clip.resize((384,216)).speedx(2) # 2 times faster
#clip = clip.resize((182,324)).speedx(2)

# saving video clip as gif
clip.write_gif("captioned_black_cat.gif")#, fps=30, program='ffmpeg')


[MoviePy] Building file captioned_black_cat.gif with imageio


 99%|█████████▉| 147/148 [00:06<00:00, 21.84it/s]
